In [ ]:
import sqlite3
from smolagents import CodeAgent, DuckDuckGoSearchTool, LiteLLMModel
from dotenv import load_dotenv
import os
import json

load_dotenv()
cohere_token = os.getenv("cohere_key")

# Define the agent
model = LiteLLMModel(
    model_id="command-r",
    api_key=cohere_token,
)
agent = CodeAgent(tools=[DuckDuckGoSearchTool()], model=model)

# Define the function to choose the best algorithm
def choose_best_algorithm(train_db_file="train_mTSP.sqlite3", test_db_file="test_mTSP.sqlite3"):

    conn_train = sqlite3.connect(train_db_file)
    cursor_train = conn_train.cursor()

    # Select instances from the training database
    cursor_train.execute("""
        SELECT instance_id, nr_cities, nr_salesmen, average_distance, stddev_distance, density, salesmen_ratio, 
               bounding_box_area, aspect_ratio, spread, cluster_compactness, mst_total_length, entropy_distance_matrix 
        FROM instances 
    """)
    train_instances = cursor_train.fetchall()
    train_instances_with_columns = [
        {
            "instance_id": row[0], 
            "nr_cities": row[1], 
            "nr_salesmen": row[2],
            "average_distance": row[3],
            "stddev_distance": row[4],
            "density": row[5],
            "salesmen_ratio": row[6],
            "bounding_box_area": row[7],
            "aspect_ratio": row[8],
            "spread": row[9],
            "cluster_compactness": row[10],
            "mst_total_length": row[11],
            "entropy_distance_matrix": row[12]
        } for row in train_instances
    ]

    # Select algorithms from the training database
    cursor_train.execute("""
        SELECT instance_id, strategy, total_cost, normalized_cost, time_taken, distance_gap, efficiency 
        FROM algorithms 
        WHERE instance_id IN (SELECT instance_id FROM instances)
    """)
    train_algorithms_data = cursor_train.fetchall()
    train_algorithms_with_columns = [
        {
            "instance_id": row[0],
            "strategy": row[1],
            "total_cost": row[2],
            "normalized_cost": row[3],
            "time_taken": row[4],
            "distance_gap": row[5],
            "efficiency": row[6],
        }
        for row in train_algorithms_data
    ]


    conn_train.close()
    conn_test = sqlite3.connect(test_db_file)
    cursor_test = conn_test.cursor()

    # Select instances from the test database
    cursor_test.execute("""
        SELECT instance_id, nr_cities, nr_salesmen, average_distance, stddev_distance, density, salesmen_ratio, 
               bounding_box_area, aspect_ratio, spread, cluster_compactness, mst_total_length, entropy_distance_matrix 
        FROM instances 
    """)
    test_instances = cursor_test.fetchall()
    test_instances_with_columns = [
        {
            "instance_id": row[0], 
            "nr_cities": row[1], 
            "nr_salesmen": row[2],
            "average_distance": row[3],
            "stddev_distance": row[4],
            "density": row[5],
            "salesmen_ratio": row[6],
            "bounding_box_area": row[7],
            "aspect_ratio": row[8],
            "spread": row[9],
            "cluster_compactness": row[10],
            "mst_total_length": row[11],
            "entropy_distance_matrix": row[12]
        } for row in test_instances
    ]

    conn_test.close()

    # Prepare the data for the agent
    data = {
        "train_instances": train_instances_with_columns,
        "train_algorithms": train_algorithms_with_columns,
        "test_instances": test_instances_with_columns,
    }
    data_str = json.dumps(data, indent=4)

    # Task for the agent
    task = f"""
    You are an AI agent tasked with selecting the best algorithm for solving each instance of the mTSP problem.
    Below is the data from the training instances and their results for different strategies:

    {data_str}

    Your task is to:
    1. Analyze the performance of each strategy (Greedy, Branch and Cut, Ant Colony, KMeans-Greedy) on the training instances.
    2. Based on this analysis, recommend the best strategy for each test instance.
    3. Justify your recommendations based on the training data.
    4. Consider the following performance metrics: total cost, normalized_cost, time taken, efficiency, and distance gap. The total cost is the most important metric, followed by normalized_cost and efficiency. Time taken is less important, but it should be considered for strategies that are computationally expensive.
    5. Take into account that Branch and Cut and Ant Colony are more computationally expensive, while Greedy and KMeans-Greedy are faster but may not always yield the best results.
    6. Branch and Cut and Ant Colony have a 100 seconds time limit, so they may output a weaker solution if the time limit is reached or even no solution at all.

    Output your recommendations in the following format:
    [
    {{ "instance_id": <test_instance_id>, "recommended_strategy": <strategy>, "justification": <reason> }}
    ]   
    """

    response = agent.run(task)
    print(response)

choose_best_algorithm(train_db_file="train_mTSP.sqlite3", test_db_file="test_mTSP.sqlite3")


c:\Users\ignat\AppData\Local\Programs\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ You are an AI agent tasked with selecting the best algorithm for solving each instance of the mTSP problem.     │
│     Below is the data from the training instances and their results for different strategies:                   │
│                                                                                                                 │
│     {                                                                                                           │
│     "train_instances": [                                                                                        │
│         {                                                                                                       │
│             "instance_id": 1,                                                                                   │
│             "nr_cities": 15,                                                                                    │
│             "nr_salesmen": 3,                                                                                   │
│             "average_distance": 6822.850650201972,                                                              │
│             "stddev_distance": 6766.0401414006865,                                                              │
│             "density": 0.7725147928217813,                                                                      │
│             "salesmen_ratio": 0.2,                                                                              │
│             "bounding_box_area": 8832.0,                                                                        │
│             "aspect_ratio": 0.9583333333333334,                                                                 │
│             "spread": 0.016425891691716515,                                                                     │
│             "cluster_compactness": 454.8567100134648,                                                           │
│             "mst_total_length": 309.276067867573,                                                               │
│             "entropy_distance_matrix": 2.7959530609379706                                                       │
│         },                                                                                                      │
│         {                                                                                                       │
│             "instance_id": 2,                                                                                   │
│             "nr_cities": 15,                                                                                    │
│             "nr_salesmen": 3,                                                                                   │
│             "average_distance": 6862.288677204529,                                                              │
│             "stddev_distance": 6805.155847429309,                                                               │
│             "density": 0.7935116416748993,                                                                      │
│             "salesmen_ratio": 0.2,                                                                              │
│             "bounding_box_area": 8648.0,                                                                        │
│             "aspect_ratio": 1.0217391304347827,                                                                 │
│             "spread": 0.018664619197186007,                                                                     │
│             "cluster_compactness": 457.4859118136353,                                                           │
│             "mst_total_length": 310.72208166143344,   

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Error in code parsing:
Your code snippet is invalid, because the regex pattern ```(?:py|python)?\n(.*?)\n``` was not found in it.
            Here is your code snippet:
            To recommend the best strategy for each test instance, I analyzed the performance of each strategy on 
the training instances based on the provided metrics. Here are the key findings and recommendations:

### Analysis of Training Instances:
1. **Total Cost**: 
   - **Branch and Cut** consistently achieves the lowest total cost across most instances, indicating it finds the 
optimal or near-optimal solution.
   - **Greedy** and **KMeans-Greedy** are faster but often yield higher total costs compared to **Branch and Cut** 
and **Ant Colony**.
   - **Ant Colony** performs well in terms of total cost, often close to **Branch and Cut**, but with higher 
variability.

2. **Normalized Cost**:
   - **Branch and Cut** again leads with the lowest normalized cost, followed by **Ant Colony**.
   - **Greedy** and **KMeans-Greedy** have higher normalized costs, especially in larger instances.

3. **Efficiency**:
   - **Branch and Cut** and **Ant Colony** have lower efficiency due to their computational complexity.
   - **Greedy** and **KMeans-Greedy** are highly efficient, with significantly lower time taken.

4. **Time Taken**:
   - **Greedy** and **KMeans-Greedy** are the fastest, often completing in negligible time.
   - **Branch and Cut** and **Ant Colony** are much slower, with **Branch and Cut** frequently hitting the 
100-second time limit, especially in larger instances.

5. **Distance Gap**:
   - **Branch and Cut** typically has the smallest distance gap, indicating it finds solutions closer to the 
optimal.
   - **Ant Colony** also performs well in this metric, while **Greedy** and **KMeans-Greedy** have larger gaps.

### Recommendations for Test Instances:
Based on the analysis, here are the recommendations for each test instance:

```json
[
    {
        "instance_id": 1,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut consistently achieves the lowest total cost and normalized cost in 
training instances, making it the best choice for optimal solutions despite its higher computational cost."
    },
    {
        "instance_id": 2,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut outperforms other strategies in terms of total cost and normalized cost, 
justifying its use despite the computational overhead."
    },
    {
        "instance_id": 3,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut provides the best total cost and normalized cost, making it the preferred 
strategy for this instance."
    },
    {
        "instance_id": 4,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut achieves the lowest total cost and normalized cost, despite its higher 
time taken, making it the best choice."
    },
    {
        "instance_id": 5,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut consistently delivers the lowest total cost and normalized cost, 
justifying its use despite the computational cost."
    },
    {
        "instance_id": 6,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut provides the best total cost and normalized cost, making it the optimal 
strategy for this instance."
    },
    {
        "instance_id": 7,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut achieves the lowest total cost and normalized cost, making it the 
preferred strategy despite its higher time taken."
    },
    {
        "instance_id": 8,
        "recommended_strategy": "Branch and Cut",
        "justification": "Branch and Cut consistently outperforms other strategies in terms of total cost and 
normalized cost, justifying its use."
    },
    {
        "instance_id": 9,
        "r

[Step 1: Duration 92.67 seconds| Input tokens: 120,314 | Output tokens: 3,459]

...

Execution logs:
True

Out: None

[Step 19: Duration 6.10 seconds| Input tokens: 126,681 | Output tokens: 10,378]

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 20 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Error in code parsing:
Your code snippet is invalid, because the regex pattern ```(?:py|python)?\n(.*?)\n``` was not found in it.
            Here is your code snippet:
            It seems like you've provided a call ID (`call_19`) and an observation with execution logs indicating 
`True`, but there is no output from the code snippet. Here’s a breakdown of what this might mean and how to 
proceed:

1. **Call ID (`call_19`)**: This is likely an identifier for a specific call or execution in a system or 
application. It helps in tracking and debugging.

2. **Observation**: The observation is `True`, which suggests that a condition or check in the code evaluated to 
`True`. This could be a success flag, a validation result, or any other boolean outcome.

3. **Execution Logs**: The logs indicate `True`, which aligns with the observation. This confirms that the 
execution reached a point where a `True` value was logged.

4. **Last Output from Code Snippet**: `None` indicates that the code snippet did not produce any output. This could
mean:
   - The code executed successfully but did not return or print anything.
   - There was an error or exception that prevented the code from completing its intended task.
   - The code was designed to perform a side effect (e.g., modifying a file, updating a database) rather than 
returning a value.

### Next Steps:
- **Check the Code**: Review the code snippet to ensure it is supposed to produce an output. If it should, debug to
find out why it’s returning `None`.
- **Logs and Debugging**: If available, examine more detailed logs or add additional logging to understand the flow
of execution.
- **Expected Behavior**: Verify what the expected output should be and compare it with the actual behavior.
- **Error Handling**: Ensure that any potential errors or exceptions are being caught and logged appropriately.

If you provide more context or the actual code snippet, I can offer more specific guidance!
            Make sure to include code with the correct pattern, for instance:
            Thoughts: Your thoughts
            Code:
            ```py
            # Your python code here
            ```<end_code>
Make sure to provide correct code blobs.

[Step 20: Duration 9.24 seconds| Input tokens: 126,706 | Output tokens: 10,765]